RuiTang
Yingshu Wang

---



#Abstract
Our mission to create Yahtzee AI solution by taking advantage of qlearning. 
Data collection program is written in C++. Right now, we are using test1 data which contains computer-generated random 1000 times game data.
The game consists of 13 rounds. In each round, the player rolls the dice and then score the roll in one of 13 categories. 


- **Ones:**The sum of dice with the number 1
- **Twos**: The sum of dice with the number 2
- **Threes:** The sum of dice with the number 3
- **Fours:** The sum of dice with the number 4
- **Fives:** The sum of dice with the number 5
- **Sixs:** The sum of dice with the number 6
- **Three Of A Kind:**	At least three dice the same ->	Sum of all dice
- **Four Of A Kind:**	At least four dice the same ->Sum of all dice
- **Full House:** Three of one number and two of another	-> 25
- **Small Straight:** Four sequential dice ->	30
- **Large Straight** :	Five sequential dice -> 40
- **Yahtzee** :All five dice the same	  -> 50 
- **Chance**	Any combination	 -> Sum of all dice
- **Bonus**	When numerical score higher than 63	 -> 35

In [ ]:
!pip install sweetviz

#install sweetviz

In [ ]:
import pandas as pd
import numpy as np
import sweetviz as sv

Read data collection from our testing model made from C++

In [ ]:
raw_data = pd.read_csv('simulation-100000.csv')

In [ ]:
raw_data.shape 
display(raw_data)
#print all data

game id  turn   dice  action  ...   kept  score change  score      expect
0              0     1  41465    Roll  ...    NaN           NaN      0  246.881363
1              0     1  44465  Reroll  ...   44.0           NaN      0  249.884079
2              0     1  44453  Reroll  ...  444.0           NaN      0  245.445343
3              0     1      0   Write  ...    NaN          12.0     12  245.445343
4              0     2  65246    Roll  ...    NaN           NaN     12  245.407654
...          ...   ...    ...     ...  ...    ...           ...    ...         ...
5098123    99999    12      0   Write  ...    NaN           0.0    215  230.194661
5098124    99999    13  55534    Roll  ...    NaN           NaN    215  238.500000
5098125    99999    13  55533  Reroll  ...  555.0           NaN    215  237.000000
5098126    99999    13  55563  Reroll  ...  555.0           NaN    215  239.000000
5098127    99999    13      0   Write  ...    NaN          24.0    239  239.000000

[5098128 rows x 9 columns]

- Game ID: the number of games
- turn: the number of turns in one game. min 1, max 13
- Dice: the computer generated random dice
- Action: player's behavior, computer generated
- Written: At the end of each turn, the category player choosen
- Kept: The dice playe keep
- Score: The player existing score
- Expect: It's a computer generated data. If the player feels lucky (has positive feedback from previous play), the expection tends to be high.

#Preprocessing Data
Seperating dive data
For example, from 34612 to dice one is 3, dice 2 is 4 ...

In [ ]:
tempa = raw_data.loc[:,['dice', 'kept']]
tempa.fillna(0,inplace=True)

def switch_int(digit):
    return lambda x: int(x) // 10 ** (5-digit) % 10 or np.nan

raw_data['RandomDiceOne'] = tempa['dice'].apply(switch_int(1))
raw_data['RandomDiceTwo'] = tempa['dice'].apply(switch_int(2))
raw_data['RandomDiceThree'] = tempa['dice'].apply(switch_int(3))
raw_data['RandomDiceFour'] = tempa['dice'].apply(switch_int(4))
raw_data['RandomDiceFive'] = tempa['dice'].apply(switch_int(5))

raw_data['KeepDiceOne'] = tempa['kept'].apply(switch_int(1))
raw_data['KeepDiceTwo'] = tempa['kept'].apply(switch_int(2))
raw_data['KeepDiceThree'] = tempa['kept'].apply(switch_int(3))
raw_data['KeepDiceFour'] = tempa['kept'].apply(switch_int(4))
raw_data['KeepDiceFive'] = tempa['kept'].apply(switch_int(5))


display(raw_data)

game id  turn   dice  ... KeepDiceThree  KeepDiceFour  KeepDiceFive
0              0     1  41465  ...           NaN           NaN           NaN
1              0     1  44465  ...           NaN           4.0           4.0
2              0     1  44453  ...           4.0           4.0           4.0
3              0     1      0  ...           NaN           NaN           NaN
4              0     2  65246  ...           NaN           NaN           NaN
...          ...   ...    ...  ...           ...           ...           ...
5098123    99999    12      0  ...           NaN           NaN           NaN
5098124    99999    13  55534  ...           NaN           NaN           NaN
5098125    99999    13  55533  ...           5.0           5.0           5.0
5098126    99999    13  55563  ...           5.0           5.0           5.0
5098127    99999    13      0  ...           NaN           NaN           NaN

[5098128 rows x 19 columns]

In [ ]:
#Find out the the score gained each turn (write action) 

if raw_data['action'].all() == 'Write':
  raw_data['score_gained'] = raw_data['score'].diff()


display(raw_data['score_gained'])

0           NaN
1           0.0
2           0.0
3          12.0
4           0.0
           ... 
5098123     0.0
5098124     0.0
5098125     0.0
5098126     0.0
5098127    24.0
Name: score_gained, Length: 5098128, dtype: float64



**Action Dic**
- Roll 1
- Reroll 2
- Write 3
- (INCASE) Else 4

```
# switch the Action string into numbers
```



Transfer Action string data (Roll, Reroll, Write) into integers

In [ ]:
def trans_action_Data(a):
  if a == 'Roll':
    return 1
  if a == 'Reroll':
    return 2
  if a == 'Write':
    return 3
  else :return 4  #incase exceptions


raw_data['action'] = raw_data['action'].apply(trans_action_Data)

In [ ]:
#original written data means Ones ->  2^0  = 1
#now we transfer into strings

def trans_written_Data(a):
  if a == 1:
    return 'Ones'
  if a == 2:
    return 'Twos'
  if a == 4:
    return 'Threes'
  if a == 8:
    return 'Fours'
  if a == 16:
    return 'Fives'
  if a == 32:
    return 'Sixs'
  if a == 64:
    return 'Chance'
  if a == 128:
    return 'ThreeOfAKind'
  if a == 256:
    return 'FourOfAKind'
  if a == 512:
    return 'FullHouse'
  if a == 1024:
    return 'SmallStraight'
  if a == 2048:
    return 'LongStraight'
  if a == 4096:
    return 'Yahtzee'
  if a == 8192:
    return 'Bonus'
  else :return np.nan

raw_data['written'] = raw_data['written'].apply(trans_written_Data)

#Organized Data Set

In [ ]:
#selected data from raw_data named data
data = raw_data.loc[:,['game id','turn', 'action', 'written', 'expect', 'RandomDiceOne','RandomDiceTwo','RandomDiceThree','RandomDiceFour','RandomDiceFive','KeepDiceOne','KeepDiceTwo'\
,'KeepDiceThree','KeepDiceFour','KeepDiceFive','score_gained']]


# data = data.replace(0, np.nan) # replace(0, np.nan)  but not the gameid
data['game id'] = data.replace(np.nan, 0)

display(data)

game id  turn  action  ... KeepDiceFour  KeepDiceFive  score_gained
0             0     1       1  ...          NaN           NaN           NaN
1             0     1       2  ...          4.0           4.0           0.0
2             0     1       2  ...          4.0           4.0           0.0
3             0     1       3  ...          NaN           NaN          12.0
4             0     2       1  ...          NaN           NaN           0.0
...         ...   ...     ...  ...          ...           ...           ...
5098123   99999    12       3  ...          NaN           NaN           0.0
5098124   99999    13       1  ...          NaN           NaN           0.0
5098125   99999    13       2  ...          5.0           5.0           0.0
5098126   99999    13       2  ...          5.0           5.0           0.0
5098127   99999    13       3  ...          NaN           NaN          24.0

[5098128 rows x 16 columns]

#Histogram

In [ ]:
import plotly.graph_objects as go
def graph(x,i):
  fig_hist = []

  fig_hist.append(go.Figure())

  fig_hist[0].add_trace(go.Histogram(x= x['turn'], name= i))
  fig_hist[0].add_trace(go.Histogram(x= x[x['score_gained']>0]['turn'], name= i + ' > 0'))
  fig_hist[0].update_layout(height=400, width=800, title_text='Result in '+ str(i) +' :Scored Gained for Different Turns')
  fig_hist[0].update_layout(barmode='overlay')
  fig_hist[0].update_traces(opacity=0.5)
  fig_hist[0].show()




list_ = data['written'].dropna().unique()

col_names =  ['name', 'turn_mean', 'score_mean']
A  = pd.DataFrame(columns = col_names)

for i in list_: 
  x = data.loc[data['written'] == i]
  x= x.loc[:,['written','turn','score_gained']]
  graph(x,i)
  print(i , "Average turns is" , x['turn'].mean() ,"Average Socres Gained is",x['score_gained'].mean())




Fours Average turns is 6.42404 Average Socres Gained is 12.26836


ThreeOfAKind Average turns is 7.62727 Average Socres Gained is 22.68595


Sixs Average turns is 6.30315 Average Socres Gained is 19.32132


FourOfAKind Average turns is 9.74171 Average Socres Gained is 13.09483


Threes Average turns is 6.63149 Average Socres Gained is 8.65089


...

Twos Average turns is 6.65322 Average Socres Gained is 5.27334


Bonus Average turns is 11.15368 Average Socres Gained is 24.24905


Ones Average turns is 6.431146314082574 Average Socres Gained is 1.8292794478400067


LongStraight Average turns is 7.33474 Average Socres Gained is 33.0072


Yahtzee Average turns is 8.68171 Average Socres Gained is 16.3865




1.   List item
2.   List item

- Blue zones mean at that turn this score type was given up
- FullHouse, Yahtzee and LongStraight have a decreasing tendency as number of turns increased. The player tends to give up Yahtzee and LongStraight in the later turns.
- Others morelikly randomly uniform 

In [ ]:

import plotly.graph_objects as go
temp = data.loc[:,['expect','score_gained']]
visualizable_feature_names = temp.columns[0:2] 


num_visualizable_features = len(visualizable_feature_names)
labels = data['written'].unique()
display(labels)


fig_hist = []
for i, feature_name in enumerate(visualizable_feature_names):
    fig_hist.append(go.Figure())
    for label in labels:
        fig_hist[i].add_trace(go.Histogram(x=data[data['written']==label][feature_name], name=label))
    fig_hist[i].update_layout(height=400, width=800, title_text=feature_name)
    fig_hist[i].update_layout(barmode='overlay')
    fig_hist[i].update_traces(opacity=0.5)
    fig_hist[i].show()

array([nan, 'SmallStraight', 'Ones', 'Sixs', 'Chance', 'LongStraight',
       'Twos', 'Threes', 'Fives', 'ThreeOfAKind', 'FourOfAKind',
       'Yahtzee', 'FullHouse', 'Fours'], dtype=object)

 - Expect for each written is almost the same. Four Of A kind has flat outcome. 
